In [7]:
import os
import pandas as pd

# 您的数据路径
data_path = "/media/ps/data/Datasets/300例心脏分割/300例勾画图像/FineTune_SAM2/Sam2_new/sam2/data_train"

# 查找CSV文件
csv_files = []
for file in os.listdir(data_path):
    if file.endswith('.csv'):
        csv_files.append(file)

print(f"找到的CSV文件: {csv_files}")

# 如果存在CSV文件，读取并显示其内容
if csv_files:
    for csv_file in csv_files:
        file_path = os.path.join(data_path, csv_file)
        print(f"\n读取文件: {csv_file}")
        try:
            df = pd.read_csv(file_path)
            print(f"CSV文件列名: {df.columns.tolist()}")
            print(f"CSV文件前5行:")
            print(df.head(5))
            print(f"CSV文件共有 {len(df)} 行")
        except Exception as e:
            print(f"读取文件出错: {e}")
else:
    print("数据目录中没有找到CSV文件")

# 检查图像和标注文件夹
images_dir = os.path.join(data_path, "JPEGImages")
annot_dir = os.path.join(data_path, "Annotations")

print(f"\n图像文件夹存在: {os.path.exists(images_dir)}")
if os.path.exists(images_dir):
    print(f"图像文件夹中的文件数量: {len(os.listdir(images_dir))}")
    print(f"图像文件夹中的前5个文件: {os.listdir(images_dir)[:5]}")

print(f"\n标注文件夹存在: {os.path.exists(annot_dir)}")
if os.path.exists(annot_dir):
    print(f"标注文件夹中的文件数量: {len(os.listdir(annot_dir))}")
    print(f"标注文件夹中的前5个文件: {os.listdir(annot_dir)[:5]}")

找到的CSV文件: ['train.csv']

读取文件: train.csv
CSV文件列名: ['ImageId', 'MaskId', 'Label', 'PointX', 'PointY']
CSV文件前5行:
                          ImageId                               MaskId Label  \
0  a4c_PatientA0030_a4c_20S_0.jpg  a4c_PatientA0030_a4c_20S_0_LV_0.png    LV   
1  a4c_PatientA0030_a4c_20S_0.jpg   a4c_PatientA0030_a4c_20S_0_M_1.png     M   
2  a4c_PatientA0030_a4c_20S_0.jpg  a4c_PatientA0030_a4c_20S_0_LA_2.png    LA   
3  a4c_PatientA0030_a4c_20S_0.jpg  a4c_PatientA0030_a4c_20S_0_RV_3.png    RV   
4  a4c_PatientA0030_a4c_20S_0.jpg  a4c_PatientA0030_a4c_20S_0_RA_4.png    RA   

   PointX  PointY  
0     373     164  
1     522     296  
2     454     404  
3     289     287  
4     334     457  
CSV文件共有 6620 行

图像文件夹存在: True
图像文件夹中的文件数量: 1808
图像文件夹中的前5个文件: ['a4c_PatientA0195_a4c_1D_141.jpg', 'a2c_PatientA0107_a2c_20S_959.jpg', 'a4c_PatientA0141_a4c_45D_508.jpg', 'a4c_PatientA0047_a4c_41D_63.jpg', 'a2c_PatientD0059_a2c_27.jsonS_996.jpg']

标注文件夹存在: True
标注文件夹中的文件数量: 6620
标注文件夹中的前5

In [3]:

import json
import base64
import numpy as np
import cv2
from PIL import Image
import io
import shutil
from shapely.geometry import Polygon
import random
import pandas as pd
from tqdm import tqdm
import matplotlib.pyplot as plt

def ensure_dir(directory):
    """确保目录存在，如果不存在则创建"""
    if not os.path.exists(directory):
        os.makedirs(directory)

def decode_base64_to_image(base64_string):
    """将Base64编码的图像数据解码为PIL图像"""
    if not base64_string or len(base64_string) < 100:  # 简单检查以避免处理截断的字符串
        return None
    
    try:
        # 尝试解码Base64字符串
        image_data = base64.b64decode(base64_string)
        image = Image.open(io.BytesIO(image_data))
        return image
    except Exception as e:
        print(f"解码Base64图像时出错: {e}")
        return None

def draw_polygon_mask(width, height, points, label):
    """根据多边形点创建二值掩码"""
    # 创建空白掩码
    mask = np.zeros((height, width), dtype=np.uint8)
    
    # 将点格式转换为OpenCV需要的格式
    points_array = np.array(points, dtype=np.int32)
    
    # 绘制填充多边形
    cv2.fillPoly(mask, [points_array], 255)
    
    return mask

def generate_point_in_mask(mask, num_points=1):
    """在掩码内生成随机点"""
    # 找到掩码中值为255的像素位置
    y_indices, x_indices = np.where(mask == 255)
    
    if len(y_indices) == 0:
        return []  # 如果掩码为空，返回空列表
    
    points = []
    for _ in range(num_points):
        # 随机选择一个位置
        idx = random.randint(0, len(y_indices) - 1)
        x, y = int(x_indices[idx]), int(y_indices[idx])
        points.append((x, y))
    
    return points

def visualize_masks(image, masks, labels, points, output_path):
    """
    可视化图像、掩码和点
    
    参数:
    - image: 原始图像 (PIL图像对象或numpy数组)
    - masks: 掩码列表 (每个掩码是numpy数组)
    - labels: 标签列表
    - points: 每个掩码中的点列表 (每个点是(x,y)元组)
    - output_path: 输出图像路径
    """
    # 确保image是numpy数组
    if isinstance(image, Image.Image):
        img_np = np.array(image)
    else:
        img_np = image.copy()
    
    # 创建可视化图像
    vis_img = img_np.copy()
    
    # 颜色映射 (标签到RGB颜色)
    color_map = {
        'LV': (255, 0, 0),    # 红色
        'LA': (0, 255, 0),    # 绿色
        'RV': (0, 0, 255),    # 蓝色
        'RA': (0, 255, 255),  # 黄色
        'M': (255, 0, 255),   # 紫色
        'unknown': (128, 128, 128)  # 灰色
    }
    
    # 创建图形和子图
    fig, axes = plt.subplots(1, 3, figsize=(18, 6))
    
    # 显示原始图像
    axes[0].imshow(img_np)
    axes[0].set_title('原始图像')
    axes[0].axis('off')
    
    # 创建合并掩码的彩色图像
    color_mask = np.zeros((*img_np.shape[:2], 3), dtype=np.uint8)
    
    # 将掩码叠加到图像上，使用不同颜色
    for mask, label, point in zip(masks, labels, points):
        # 获取标签对应的颜色
        color = color_map.get(label, color_map['unknown'])
        
        # 添加掩码颜色
        for i in range(3):
            color_mask[:, :, i][mask > 0] = color[i]
    
    # 显示彩色掩码
    axes[1].imshow(color_mask)
    axes[1].set_title('掩码 (不同颜色)')
    axes[1].axis('off')
    
    # 将掩码和点叠加到图像上
    overlay = img_np.copy()
    for mask, label, point in zip(masks, labels, points):
        # 获取标签对应的颜色
        color = color_map.get(label, color_map['unknown'])
        
        # 叠加掩码
        for i in range(3):
            overlay[:, :, i] = np.where(mask > 0, 
                                      (overlay[:, :, i] * 0.7 + color[i] * 0.3).astype(np.uint8), 
                                      overlay[:, :, i])
        
        # 在图像上标记点
        if point:
            # 绘制点
            cv2.circle(overlay, point, 5, (255, 255, 255), -1)  # 白色实心圆
            # 确保点在图像内
            y, x = point[1], point[0]
            if 0 <= y < overlay.shape[0] and 0 <= x < overlay.shape[1]:
                cv2.circle(overlay, point, 5, (0, 0, 0), 1)  # 黑色圆边框
    
    # 显示带有掩码和点的图像
    axes[2].imshow(overlay)
    axes[2].set_title('带有掩码和点的图像')
    for i, (label, color) in enumerate(color_map.items()):
        if label in labels:
            # 将RGB颜色转换为0-1范围
            normalized_color = [c/255 for c in color]
            axes[2].plot([], [], 'o', color=normalized_color, label=label)
    axes[2].legend(loc='upper right')
    axes[2].axis('off')
    
    # 保存图像
    plt.tight_layout()
    plt.savefig(output_path)
    plt.close(fig)

def process_json_file(json_file, output_dir, index, subdir=""):
    """处理单个JSON文件，生成图像和掩码"""
    try:
        with open(json_file, 'r') as f:
            data = json.load(f)
        
        # 提取文件名（不含扩展名）
        base_name = os.path.splitext(os.path.basename(json_file))[0]
        
        # 使用子目录和索引创建唯一文件名
        if subdir:
            unique_id = f"{subdir}_{base_name}_{index}"
        else:
            unique_id = f"{base_name}_{index}"
        
        # 解码Base64图像
        image_data = data.get('imageData', '')
        image = decode_base64_to_image(image_data)
        
        if image is None:
            print(f"无法解码图像: {json_file}")
            return None
        
        # 获取图像尺寸
        width, height = image.size
        
        # 保存原始图像
        image_path = os.path.join(output_dir, 'JPEGImages', f"{unique_id}.jpg")
        image.save(image_path)
        
        shapes = data.get('shapes', [])
        
        # 用于存储每个掩码的信息
        mask_info = []
        
        # 存储可视化相关的数据
        all_masks = []
        all_labels = []
        all_points = []
        
        # 处理每个形状/掩码
        for i, shape in enumerate(shapes):
            label = shape.get('label', 'unknown')
            points = shape.get('points', [])
            
            if not points:
                continue
                
            # 创建掩码
            mask = draw_polygon_mask(width, height, points, label)
            
            # 生成掩码文件名
            mask_filename = f"{unique_id}_{label}_{i}.png"
            mask_path = os.path.join(output_dir, 'Annotations', mask_filename)
            
            # 保存掩码
            cv2.imwrite(mask_path, mask)
            
            # 在掩码内生成一个随机点
            random_points = generate_point_in_mask(mask)
            
            if random_points:
                mask_info.append({
                    'ImageId': f"{unique_id}.jpg",
                    'MaskId': mask_filename,
                    'Label': label,
                    'PointX': random_points[0][0],
                    'PointY': random_points[0][1]
                })
                
                # 存储可视化数据
                all_masks.append(mask)
                all_labels.append(label)
                all_points.append(random_points[0])
        
        # 如果有掩码，则随机可视化一个
        if all_masks:
            # 创建可视化目录
            vis_dir = os.path.join(output_dir, 'Visualization')
            ensure_dir(vis_dir)
            
            # 随机选择可视化
            if random.random() < 0.2:  # 20%的概率进行可视化
                vis_path = os.path.join(vis_dir, f"{unique_id}_visualization.png")
                visualize_masks(image, all_masks, all_labels, all_points, vis_path)
        
        return mask_info
    
    except Exception as e:
        print(f"处理文件 {json_file} 时出错: {e}")
        import traceback
        traceback.print_exc()
        return None

def get_all_json_files(root_dir):
    """递归获取目录及其子目录中的所有JSON文件"""
    json_files = []
    subdirs = []
    
    # 遍历目录
    for dirpath, dirnames, filenames in os.walk(root_dir):
        rel_path = os.path.relpath(dirpath, root_dir)
        if rel_path == '.':
            rel_path = ''
            
        # 获取子目录名称（仅一级子目录）
        if dirpath == root_dir:
            subdirs.extend(dirnames)
            
        # 添加JSON文件和它们的相对路径
        for filename in filenames:
            if filename.endswith('.json'):
                json_files.append((os.path.join(dirpath, filename), rel_path))
    
    return json_files, subdirs

def create_dataset_structure(json_dir, output_dir):
    """创建SAM模型训练所需的数据集结构"""
    # 清空并创建输出目录
    if os.path.exists(output_dir):
        shutil.rmtree(output_dir)
    
    # 创建必要的子目录
    ensure_dir(os.path.join(output_dir, 'JPEGImages'))
    ensure_dir(os.path.join(output_dir, 'Annotations'))
    ensure_dir(os.path.join(output_dir, 'Visualization'))
    
    # 获取所有JSON文件和子目录
    json_files, subdirs = get_all_json_files(json_dir)
    
    print(f"找到 {len(json_files)} 个JSON文件在目录: {json_dir}")
    print(f"子目录: {subdirs}")
    
    all_mask_info = []
    
    # 处理每个JSON文件
    for i, (json_file, subdir) in enumerate(tqdm(json_files, desc="处理文件")):
        mask_info = process_json_file(json_file, output_dir, i, subdir)
        if mask_info:
            all_mask_info.extend(mask_info)
    
    # 创建CSV文件
    df = pd.DataFrame(all_mask_info)
    csv_path = os.path.join(output_dir, 'train.csv')
    df.to_csv(csv_path, index=False)
    
    print(f"数据集创建完成! 总共处理了 {len(json_files)} 个文件，生成了 {len(all_mask_info)} 个掩码。")
    print(f"图像保存在: {os.path.join(output_dir, 'JPEGImages')}")
    print(f"掩码保存在: {os.path.join(output_dir, 'Annotations')}")
    print(f"可视化结果保存在: {os.path.join(output_dir, 'Visualization')}")
    print(f"训练CSV文件: {csv_path}")

# 示例用法
if __name__ == "__main__":
    # 如果你有JSON文件目录
    json_dir = "/media/ps/data/Datasets/300例心脏分割/300例勾画图像/FineTune_SAM2/sam2/sam2/data/heart_chambers_dataset"  # 替换为你的JSON文件目录
    output_dir = "/media/ps/data/Datasets/300例心脏分割/300例勾画图像/FineTune_SAM2/Sam2_new/sam2/data_train"
    create_dataset_structure(json_dir, output_dir)
    


找到 1808 个JSON文件在目录: /media/ps/data/Datasets/300例心脏分割/300例勾画图像/FineTune_SAM2/sam2/sam2/data/heart_chambers_dataset
子目录: ['a4c', 'a2c', 'a3c']


处理文件:   0%|          | 3/1808 [00:00<01:03, 28.51it/s]/tmp/ipykernel_2248352/1538416663.py:151: UserWarning: Glyph 21407 (\N{CJK UNIFIED IDEOGRAPH-539F}) missing from font(s) DejaVu Sans.
  plt.tight_layout()
/tmp/ipykernel_2248352/1538416663.py:151: UserWarning: Glyph 22987 (\N{CJK UNIFIED IDEOGRAPH-59CB}) missing from font(s) DejaVu Sans.
  plt.tight_layout()
/tmp/ipykernel_2248352/1538416663.py:151: UserWarning: Glyph 22270 (\N{CJK UNIFIED IDEOGRAPH-56FE}) missing from font(s) DejaVu Sans.
  plt.tight_layout()
/tmp/ipykernel_2248352/1538416663.py:151: UserWarning: Glyph 20687 (\N{CJK UNIFIED IDEOGRAPH-50CF}) missing from font(s) DejaVu Sans.
  plt.tight_layout()
/tmp/ipykernel_2248352/1538416663.py:151: UserWarning: Glyph 25513 (\N{CJK UNIFIED IDEOGRAPH-63A9}) missing from font(s) DejaVu Sans.
  plt.tight_layout()
/tmp/ipykernel_2248352/1538416663.py:151: UserWarning: Glyph 30721 (\N{CJK UNIFIED IDEOGRAPH-7801}) missing from font(s) DejaVu Sans.
  plt.tight_layout()
/tmp/ipykernel_2

处理文件: 100%|██████████| 1808/1808 [02:45<00:00, 10.89it/s]

数据集创建完成! 总共处理了 1808 个文件，生成了 6620 个掩码。
图像保存在: /media/ps/data/Datasets/300例心脏分割/300例勾画图像/FineTune_SAM2/Sam2_new/sam2/data_train/JPEGImages
掩码保存在: /media/ps/data/Datasets/300例心脏分割/300例勾画图像/FineTune_SAM2/Sam2_new/sam2/data_train/Annotations
可视化结果保存在: /media/ps/data/Datasets/300例心脏分割/300例勾画图像/FineTune_SAM2/Sam2_new/sam2/data_train/Visualization
训练CSV文件: /media/ps/data/Datasets/300例心脏分割/300例勾画图像/FineTune_SAM2/Sam2_new/sam2/data_train/train.csv
